# Klausur Finanz- und Sozialpolitik, Sommersemester 2023

## 21. Juli 2023, 9:00 – 11:00 Uhr

### Allgemeines

- Sie haben 120 Minuten Zeit zum Bearbeiten der Klausur, und anschließend weitere 60
  Minuten zum Hochladen des Notebooks auf eCampus. Wir erwarten jedoch, dass keine
  technischen Probleme beim Hochladen auftreten und sind gern behilflich, wenn Sie
  Schwierigkeiten haben. 
- Sie können maximal 150 Punkte erreichen. Den Kurs können Sie nur bestehen, wenn Sie
  mindestens 75 Punkte **in der Klausur** erreichen. In dem Fall werden etwaige
  Extrapunkte aus dem Semester hinzugezählt.
- In der Klausur sind alle Hilfsmittel erlaubt, nur gemeinsames Arbeiten ist strikt
  verboten.
- Wir empfehlen Ihnen, sich **jetzt** eine Kopie der Originalklausur zu erstellen, falls
  Sie ausversehen Zellen löschen. Sie können natürlich auch jederzeit wieder die Version
  von eCampus bzw. der Website herunterladen.

### Bearbeitungshinweise

- Sie können nur eine einzige Datei hochladen, beantworten Sie deshalb alle Fragen in
  diesem Notebook.
- Bei allen Fragen geben wir Ihnen Code- und / oder Markdownzellen für Ihre Antworten
  vor.
  - Wenn nur eine Codezelle vorhanden ist, erwarten wir auch nur eine Berechnung oder
    Graphik als Antwort.
  - Wenn nur eine Markdownzelle vorhanden ist, erwarten wir nur eine verbale Antwort.
  - Wenn beide Arten von Zellen vorhanden sind, erwarten wir sowohl eine Berechnung oder
    Graphik als auch eine verbale Antwort.
- Um Ihre Lösung nachzuvollziehen, ist es wichtig, dass in der abgegebenen Version die
  ausgeführten Zellen fortlaufend von 1 bis N nummeriert sind. **Vor der Abgabe lassen
  Sie daher bitte die bearbeitete Klausur per "Kernel" -> "Restart Kernel and Run all
  Cells" durchlaufen und speichern Sie das Notebook anschließend.**

### Abgabe und Rücktritt

- Wenn Sie nicht abgeben möchten, stellen Sie bitte sicher, dass keine Datei
  hochgeladen ist.

**Viel Erfolg!**

## Import der Bibliotheken

In [ ]:
from pathlib import Path

import numpy as np
import pandas as pd

pd.options.plotting.backend = "plotly"

from gettsim import (
    compute_taxes_and_transfers,
    create_synthetic_data,
    set_up_policy_environment,
)

DATA = Path("/tmp/Daten_FSP/")  # noqa: S108

## Einführung

Vor zwei Wochen forderte Monika Schnitzer, Vorsitzende des Sachverständigenrates zur Begutachtung der gesamtwirtschaftlichen Entwicklung, u.a. die [Abschaffung der Familienversicherung für Ehepartner:innen innerhalb der gesetzlichen Krankenversicherung](https://www.spiegel.de/wirtschaft/rente-wirtschaftsweise-monika-schnitzer-will-witwenrente-abschaffen-a-d76aa7db-648e-4d2b-b3dc-1dd9e2f6f6a7):

> _Auf der Podiumsdiskussion des IZA machte Schnitzer sich zudem erneut für eine Abschaffung der kostenlosen Mitversicherung in der Krankenkasse für nicht erwerbstätige Ehepartner stark. Die Ökonomin äußerte sich vor dem Hintergrund der Probleme, die der demografische Wandel für den Arbeitsmarkt und die Sozialversicherungen darstellt. So erfordert beispielsweise der Fachkräftemangel höhere Investitionen etwa in die Qualifizierung von Arbeitslosen oder die Ausweitung von Kinderbetreuung, um Eltern eine Erweiterung ihrer Erwerbstätigkeit zu ermöglichen._

In dieser Klausur werden Sie die Effekte einer solchen Reform analysieren und Vor- und Nachteile diskutieren. Da die im Kurs verwendeten SOEP-Daten aus dem Jahr 2019 stammen, analysieren wir die Effekte der Reform mit dem Ausgangsjahr 2019.

Derzeit können Erwerbstätige ihre:n Ehepartner:in kostenlos in der Krankenversicherung mitversichern, sofern die mitzuversichernde Person ein monatliches Einkommen unterhalb der Geringfügigkeitsgrenze ("Minijob", also maximal 450€  im Jahr 2019) erhält. Sofern eine Person weniger als 450€ monatlich verdient, eine kostenlose Familienversicherung aber nicht möglich ist (bspw. weil unverheiratet oder Ehepartner:in nicht regulär krankenversichert), kann sie sich freiwillig in der gesetzlichen Krankenversicherung versichern (es herrscht Krankenversicherungspflicht; die Alternative einer privaten Versicherung lassen wir außer Acht).

Für die Beiträge einer freiwillig in der gesetzlichen Krankenversicherung versicherten Person werden ihre Einkünfte herangezogen. Falls diese sehr gering sind, gilt jedoch eine [Mindestbemessungsgrenze](https://www.krankenkasseninfo.de/zahlen-fakten/lexikon/mindestbemessungsgrenze). Diese betrug im Jahr 2019 1038,38 € monatlich. Wenn das Einkommen der freiwillig versicherten Person darunter liegt, wird dieser Betrag als Grundlage für die Berechnung des KV Beitrags angesetzt. Der durchschnittliche Beitragssatz im Jahr 2019 (mit Zusatzbeitrag) betrug 15.5%.

Der monatliche Beitrag zur freiwilligen Krankenversicherung betrug 2019 für geringfügig Beschäftigte daher monatlich 160,94€. Empfänger von Arbeitslosengeld 2 sind innerhalb der gesetzlichen Krankenversicherung pflichtversichert, die Kosten werden also übernommen. Ab dem Midijob-Bereich (monatliches Einkommen > 450€) greift die Pflichtversicherung in der gesetzlichen Krankenversicherung.

Da wir keinen ausgearbeiteten Reformvorschlag gefunden haben, gehen wir von folgendem Reformszenario aus: Anstelle der kostenlosen Mitversicherung müssen sich die vormals kostenlos Versicherten nun freiwillig für 160,94€ versichern, um einen Versicherungsschutz zu erhalten. Alle anderen Parameter des deutschen Steuer- und Abgabensystems bleiben unverändert.

Zur Vereinfachung treffen wir folgende Annahmen:
1. Jede Person ist gesetzlich krankenversichert.
2. Sofern eine Person in der gesetzlichen Krankenversicherung nicht pflichtversichert ist, versichert sie sich freiwillig. Jede Person ist also krankenversichert.
3. Im Reformszenario wirkt sich die freiwillige Krankenversicherung nicht auf die ALG 2 Ansprüche der Person aus. Das ist die derzeitige gesetzliche Regelung.
4. Erwachsene, die zusammen in einem Haushalt leben, sind verheiratet und können sich im Status Quo deshalb familienversichern.

## Aufgabe 1: Bundeszuschuss zur Finanzierung der Gesetzlichen Krankenversicherung (6 Punkte)

Jedes Jahr bezuschusst der Bund den sogenannten Gesundheitsfonds aus Steuermitteln zur Finanzierung der gesetzlichen Krankenversicherung. Recherchieren Sie im Internet die Höhe des gesamten Bundeszuschusses zum Gesundheitsfonds im Jahr 2019. Geben Sie die Zahl in Milliarden Euro mit einer Nachkommastelle sowie eine Quelle an (Internetlink ist ausreichend).

## Aufgabe 2: Effekte der Reform auf Abgaben (insgesamt 40 Punkte)

Um die Wirkung der Reform zu beschreiben, betrachten wir zunächst synthetische Daten. Im
Folgenden erstellen wir einen Datensatz aus Nebenverdienenden, die sich in ihrem
Bruttolohn unterscheiden. Wir nehmen an, dass die jeweiligen Hauptverdienenden des
Haushalts ihre/n Ehepartner/in familienversichern können.

In [ ]:
minijob_grenze = 450.0
min_einkommen = 0
max_einkommen = 7_000
anzahl_schritte = 701

_bruttolohn_m = np.linspace(min_einkommen, max_einkommen, anzahl_schritte)

synthetische_daten = create_synthetic_data(
    n_adults=1,
    n_children=0,
    specs_heterogeneous={
        "bruttolohn_m": [[i] for i in _bruttolohn_m],
    },
    specs_constant_over_households={
        "Hauptverdiener": [False],
    },
)

# Neue Spalte, die wir aufgrund unserer Modifikationen an GETTSIM benötigen.
synthetische_daten["hauptverdiener_versichert"] = True

Im zweiten Teil der Klausur werden wir SOEP Daten aus dem Jahr 2019 nutzen. Deshalb setzen wir die Parameter des Steuer- und Transfersystems auf die des Jahres 2019 fest.

Die kostenlose Mitversicherung von Ehepartnern ist in GETTSIM derzeit nicht
implementiert. 

Wir fügen daher eine Funktion hinzu, die den Krankenversicherungsbeitrag im Status quo
ausgibt. Wie oben beschrieben nehmen wir an, dass *alle* Personen versichert sind.
Entweder über die/den Hauptverdiener:in in der Familienversicherung, freiwillig mit
einem Beitrag von 160,94€ oder "ganz normal" bei einem Einkommen oberhalb der Minijobgrenze
(in 2019: 450€).

In [ ]:
def krankenv_beitr_status_quo_m(
    geringfügig_beschäftigt,
    kind,
    hauptverdiener_versichert,
    ges_krankenv_beitr_m,
):
    """Krankenversicherungsbeitrag im Status Quo.

    Implementiert die freiwillige Krankenversicherung (KV) und die Familienversicherung
    zusätzlich zur Pflichtversicherung.
    Pflichtversicherungsbeiträge werden durch die Funktion `ges_krankenv_beitr_m`
    berechnet.

    Args:
        geringfügig_beschäftigt (bool): Ob Person einen Minijob hat.
        kind (bool): True, wenn Person ein Kind im Sinne des BKGG ist.
        hauptverdiener_versichert (bool): True, wenn ein/e regulär
            versicherte/r Hauptverdiener:in im Haushalt ist.
        ges_krankenv_beitr_m (float): Pflichtversicherungsbeitrag der
            Person.
    """
    if kind or geringfügig_beschäftigt and hauptverdiener_versichert:
        out = 0.0
    elif geringfügig_beschäftigt:
        out = 160.94
    else:
        out = ges_krankenv_beitr_m
    return out

Nun rufen wir GETTSIM auf.

Funktionen und Parameter übernehmen wir direkt aus dem Steuersystem: `policy_func_dict` und `params_dict`. Außerdem ergänzen wir unsere Funktion `krankenv_beitr_status_quo_m`. Als Target wählen wir ebenfalls unsere Funktion (nicht die in GETTSIM implementierte), die uns den monatlichen Beitrag zur gesetzlichen Krankenversicherung ausgeben wird.

In [ ]:
params_dict, policy_func_dict = set_up_policy_environment(2019)

In [ ]:
synthetische_ergebnisse_status_quo = compute_taxes_and_transfers(
    data=synthetische_daten,
    params=params_dict,
    functions=[
        policy_func_dict,
        {"krankenv_beitr_m": krankenv_beitr_status_quo_m},
    ],
    targets=["krankenv_beitr_m"],
)

# Der Bruttolohn wird wieder an dem DataFrame hinzugefügt.
synthetische_ergebnisse_status_quo = synthetische_ergebnisse_status_quo.join(
    synthetische_daten["bruttolohn_m"],
)

synthetische_ergebnisse_status_quo

### Aufgabe 2.1: Krankenversicherungsbeiträge im Status Quo (insgesamt 13 Punkte)

#### Aufgabe 2.1.1: Grafische Darstellung (5 Punkte)

Plotten Sie den Krankenversicherungsbeitrag der/s Nebenverdienenden in Abhängigkeit ihres/seines Bruttolohns.

#### Aufgabe 2.1.2: Erklärung des Abgabenprofils (8 Punkte)

Erklären Sie die wichtigsten Merkmale der in der obigen Zelle erstellten Abbildung. Sie können den Sprung der Krankenversicherungsbeiträge bei einem Bruttolohn von 460€ ignorieren.

### Aufgabe 2.2: Krankenversicherungsbeiträge im Reformszenario (insgesamt 27 Punkte)
#### Aufgabe 2.2.1: Implementierung der neuen Regeln (8 Punkte)

Jetzt möchten wir die Krankenversicherungsbeiträge nach der Reform berechnen. Das heißt die Option der Mitversicherung über den Hauptverdiener entfällt und die vorher Familienversicherten versichern sich stattdessen freiwillig. Definieren Sie eine neue Funktion, die dies implementiert. Nutzen Sie die Funktion `krankenv_beitr_status_quo_m` als Ausgangspunkt. Nennen Sie Ihre neue Funktion `krankenv_beitr_reform_m`.

Wir ersetzen die Funktion mit Ihrer neuen `krankenv_beitr_reform_m` Funktion und lassen GETTSIM die Beiträge nach der Reform berechnen.

In [ ]:
synthetische_ergebnisse_reform = compute_taxes_and_transfers(
    data=synthetische_daten,
    params=params_dict,
    functions=[
        policy_func_dict,
        {"krankenv_beitr_m": krankenv_beitr_reform_m},
    ],
    targets=["krankenv_beitr_m"],
)

# Der Bruttolohn wird wieder an das DataFrame gejoint.
synthetische_ergebnisse_reform = synthetische_ergebnisse_reform.join(
    synthetische_daten[["bruttolohn_m"]],
)

synthetische_ergebnisse_reform

#### Aufgabe 2.2.2: Grafische Darstellung (5 Punkte)

Plotten Sie den Beitrag des Zweitverdienenden nach der Reform in Abhängigkeit des Bruttolohns.

#### Aufgabe 2.2.3: Erklärung des Abgabenprofils (4 Punkte)

Erklären Sie die wichtigsten Merkmale der in der obigen Zelle erstellten Abbildung.

In [ ]:
synthetische_ergebnisse_reform = (
    synthetische_ergebnisse_reform.reset_index()
    .set_index(["bruttolohn_m"])
    .drop(columns=["index"])
)
synthetische_ergebnisse_status_quo = (
    synthetische_ergebnisse_status_quo.reset_index()
    .set_index(["bruttolohn_m"])
    .drop(columns=["index"])
)


synthetische_ergebnisse = pd.concat(
    [synthetische_ergebnisse_reform, synthetische_ergebnisse_status_quo],
    keys=["Reform", "Status Quo"],
    names=["Szenario"],
)

synthetische_ergebnisse

#### Aufgabe 2.2.4: Auswirkung der Reform auf Abgaben des Nebenverdieners (10 Punkte)

Berechnen Sie die Differenz der Beiträge nach und vor der Reform und plotten Sie diese in Abhängigkeit des Bruttolohns.

## Aufgabe 3: Anreizwirkung der Reform (10 Punkte)

Erläutern Sie: Wie wirkt sich die Reform auf die Arbeitsanreize des Nebenverdienenden aus?

## Aufgabe 4: Verteilungseffekte (insgesamt 46 Punkte)
### Aufgabe 4.1: Ungleichheit im Status Quo (insgesamt 12 Punkte)

Nun wollen wir die Reform mittels GETTSIM und basierend auf den SOEP Daten von 2019 simulieren. Dazu betrachten wir zunächst den Status Quo.

Die folgenden Zellen lesen die Daten ein und verarbeiten sie. Sie brauchen diese nicht im Detail durchzugehen, sie führen die gleichen Operationen aus wie in der Präsenzphase.

In [ ]:
soep_daten = pd.read_pickle(DATA / "gettsim_data_soep_2019.pkl")  # noqa: S301

soep_daten["hh_id"] = soep_daten["hh_id"].astype(int)
soep_daten["tu_id"] = soep_daten["tu_id"].astype(int)

soep_daten = soep_daten.reset_index()

# Wähle 4_000 Haushalte aus.
_rng = np.random.default_rng(seed=9)
random_households = _rng.choice(soep_daten["hh_id"].unique(), size=4_000)
soep_daten = soep_daten.query("hh_id in @random_households")


soep_daten = soep_daten.drop(["anz_kinder_hh"], axis=1)

mask = soep_daten.groupby("hh_id")["rentner"].transform(any)
soep_daten = soep_daten[~mask]

anz_kinder_bis_13 = (
    soep_daten.query("alter < 14 & kind == True").groupby("hh_id").size()
).to_frame("anz_kinder_bis_13")

anz_kinder_ab_14 = (
    soep_daten.query("alter >= 14 & kind == True").groupby("hh_id").size()
).to_frame("anz_kinder_ab_14")

anz_erwachsene = (soep_daten.query("kind == False").groupby("hh_id").size()).to_frame(
    "anz_erwachsene",
)

soep_daten = soep_daten.set_index("hh_id").join(
    [
        anz_kinder_bis_13,
        anz_kinder_ab_14,
        anz_erwachsene,
    ],
)

soep_daten["anz_kinder_bis_13"] = soep_daten["anz_kinder_bis_13"].fillna(0).astype(int)
soep_daten["anz_kinder_ab_14"] = soep_daten["anz_kinder_ab_14"].fillna(0).astype(int)

# GETTSIM unterstützt nur eine tax unit pro Haushalt.
soep_daten = soep_daten.reset_index()
soep_daten["hh_id"] = soep_daten["tu_id"]

# Fehlende Werte auf 0 setzen.
for c in [
    "kindergeld_hh",
    "kinderzuschlag_hh",
    "grundr_zeiten",
    "grundr_bew_zeiten",
    "bruttolohn_vorj_m",
]:
    soep_daten[c] = soep_daten[c].fillna(0)

# Jahresangaben runden
for c in [
    "jahr_renteneintr",
    "immobilie_baujahr_hh",
    "grundr_zeiten",
    "grundr_bew_zeiten",
]:
    soep_daten[c] = soep_daten[c].round(0)

# Boolean Datentyp
for c in [
    "weiblich",
    "wohnort_ost",
    "anwartschaftszeit",
]:
    soep_daten[c] = soep_daten[c].astype(bool)

# Integer Datentyp
for c in [
    "alter",
    "geburtsmonat",
    "geburtsjahr",
    "jahr_renteneintr",
    "m_elterngeld",
    "behinderungsgrad",
    "immobilie_baujahr_hh",
    "grundr_zeiten",
    "grundr_bew_zeiten",
]:
    soep_daten[c] = soep_daten[c].astype(int)

# Float Datentyp
for c in ["sozialv_pflicht_5j"]:
    soep_daten[c] = soep_daten[c].astype(float)

# Unbekannte Werte zu 0
for c in [
    "m_pflichtbeitrag",
    "m_freiw_beitrag",
    "m_mutterschutz",
    "m_arbeitsunfähig",
    "m_krank_ab_16_bis_24",
    "m_arbeitslos",
    "m_ausbild_suche",
    "m_schul_ausbild",
    "m_geringf_beschäft",
    "m_alg1_übergang",
    "m_ersatzzeit",
    "m_kind_berücks_zeit",
    "m_pfleg_berücks_zeit",
    "y_pflichtbeitr_ab_40",
    "kind_unterh_anspr_m",
]:
    soep_daten[c] = 0.0

soep_daten["bruttolohn_vorj_m"] = soep_daten["bruttolohn_vorj_m"].replace(np.inf, 0)

Jetzt erstellen wir eine Spalte, die angibt, ob der/die Hauptverdiener:in versichert ist.

In [ ]:
soep_daten["hauptverdiener_versichert"] = np.where(
    soep_daten["bruttolohn_m"] > minijob_grenze,
    True,  # noqa: FBT003
    False,  # noqa: FBT003
)
soep_daten["hauptverdiener_versichert"] = soep_daten.groupby("hh_id")[
    "hauptverdiener_versichert"
].transform(any)

soep_daten = soep_daten.reset_index().set_index(["p_id", "hh_id", "tu_id"])

Nun berechnen wir mit Hilfe von GETTSIM und für die SOEP Daten die Steuern und Abgaben im Status Quo.

In [ ]:
gettsim_ergebnisse_status_quo = compute_taxes_and_transfers(
    data=soep_daten.reset_index(),
    params=params_dict,
    functions=[
        policy_func_dict,
        {"krankenv_beitr_m": krankenv_beitr_status_quo_m},
    ],
    targets=[
        "kindergeld_m_hh",
        "sozialv_beitr_m",
        "arbeitsl_geld_m",
        "arbeitsl_geld_2_m_hh",
        "wohngeld_m_hh",
        "kinderzuschl_m_hh",
        "eink_st_tu",
        "soli_st_tu",
        "sum_eink_tu",
        "krankenv_beitr_m",
        "ges_pflegev_beitr_m",
        "ges_rentenv_beitr_m",
        "arbeitsl_v_beitr_m",
    ],
)

# Wir joinen die Haushalts-ID and die GETTSIM Ergebnisse.
gettsim_ergebnisse_status_quo = gettsim_ergebnisse_status_quo.join(
    soep_daten.reset_index()["hh_id"],
)

gettsim_ergebnisse_status_quo

Wir betrachten die Verteilungseffekte der Reform. Dafür berechnen wir das verfügbare
Einkommen vor der Reform. Wie Sie es aus den Präsenzphasen kennen, bestimmen wir
zunächst die Steuern und Transfers auf Haushalts- und Monatsebene. Außerdem fügen wir
zusätzliche Spalten aus den SOEP Daten zu den berechneten Steuer- und Transferdaten
hinzu.

In [ ]:
ergebnisse_status_quo = (
    gettsim_ergebnisse_status_quo.reset_index()
    .groupby("hh_id")
    .agg(
        {
            "kindergeld_m_hh": lambda x: x.max(),
            "eink_st_tu": lambda x: x.max() / 12,
            "soli_st_tu": lambda x: x.max() / 12,
            "arbeitsl_geld_2_m_hh": lambda x: x.max(),
            "arbeitsl_geld_m": lambda x: x.sum(),
            "wohngeld_m_hh": lambda x: x.max(),
            "kinderzuschl_m_hh": lambda x: x.max(),
            "sum_eink_tu": lambda x: x.max() / 12,
            "krankenv_beitr_m": lambda x: x.sum(),
            "ges_pflegev_beitr_m": lambda x: x.sum(),
            "ges_rentenv_beitr_m": lambda x: x.sum(),
            "arbeitsl_v_beitr_m": lambda x: x.sum(),
        },
    )
)

# Variablen korrekt benennen
ergebnisse_status_quo = ergebnisse_status_quo.rename(
    columns={
        "eink_st_tu": "einkommensteuer_m_tu",
        "soli_st_tu": "soli_m_tu",
        "arbeitsl_geld_m": "arbeitsl_geld_m_hh",
        "sum_eink_tu": "bruttolohn_m_hh",
        "krankenv_beitr_m": "krankenv_beitr_m_hh",
        "ges_pflegev_beitr_m": "ges_pflegev_beitr_m_hh",
        "ges_rentenv_beitr_m": "ges_rentenv_beitr_m_hh",
        "arbeitsl_v_beitr_m": "arbeitsl_v_beitr_m_hh",
    },
)

ergebnisse_status_quo = (
    ergebnisse_status_quo.join(
        soep_daten[
            [
                "hh_gewicht",
                "kapital_eink_m_hh",
                "anz_erwachsene",
                "anz_kinder_bis_13",
                "anz_kinder_ab_14",
            ]
        ],
    )
    .reset_index()
    .drop_duplicates(["hh_id"])
)

ergebnisse_status_quo["verfügbares_einkommen_m_hh"] = (
    ergebnisse_status_quo["bruttolohn_m_hh"]
    + ergebnisse_status_quo["kapital_eink_m_hh"]
    + ergebnisse_status_quo["kindergeld_m_hh"]
    + ergebnisse_status_quo["arbeitsl_geld_m_hh"]
    + ergebnisse_status_quo["arbeitsl_geld_2_m_hh"]
    + ergebnisse_status_quo["kinderzuschl_m_hh"]
    + ergebnisse_status_quo["wohngeld_m_hh"]
    - ergebnisse_status_quo["einkommensteuer_m_tu"]
    - ergebnisse_status_quo["soli_m_tu"]
    - ergebnisse_status_quo["krankenv_beitr_m_hh"]
    - ergebnisse_status_quo["ges_pflegev_beitr_m_hh"]
    - ergebnisse_status_quo["ges_rentenv_beitr_m_hh"]
    - ergebnisse_status_quo["arbeitsl_v_beitr_m_hh"]
)

Um das Nettoäquivalenzeinkommen zu berechnen, nutzen wir die OECD-Skala, die Sie bereits kennen.

In [ ]:
def oecd_skala(data):
    """Berechne Gewichtungsfaktor für OECD-Äquivalenzskala.

    Args:
        data (pd.DataFrame): Datensatz mit Spalten für Anzahl Erwachsene und Kinder.

    Returns:
        pd.Series: Gewichtungsfaktor für OECD-Äquivalenzskala.
    """
    return (
        1
        + 0.5 * (data["anz_erwachsene"] + data["anz_kinder_ab_14"] - 1)
        + 0.3 * data["anz_kinder_bis_13"]
    )

#### Aufgabe 4.1.1: Berechnung des Nettoäquivalenzeinkommens (10 Punkte)

Bestimmen Sie das verfügbare Nettoäquivalenzeinkommen mit der OECD Gewichtung. Nennen Sie die Spalte `Nettoäquivalenzeinkommen`.

#### Aufgabe 4.1.2: Berechnung des Gini-Koeffizienten (2 Punkte)

Berechnen Sie den Gini-Koeffizienten mit der unten gegebenen Funktion. 

*Hinweis: Der Gini Koeffizient ist aufgrund unserer simplifizierenden Annahmen zu hoch. Gute Schätzungen kommen für Deutschland auf 0,3.*

In [ ]:
def gini(einkommen):
    """Berechnet den Gini-Koeffizienten.

    Args:
        einkommen (pd.Series): Einkommen
    Returns:
        float: Gini-Koeffizient
    """
    einkommen_sortiert = einkommen.sort_values()
    n = einkommen_sortiert.size
    coef = 2 / n
    const = (n + 1) / n
    weighted_sum = sum([(i + 1) * yi for i, yi in enumerate(einkommen_sortiert)])
    return coef * weighted_sum / (einkommen_sortiert.sum()) - const

### Aufgabe 4.2: Charakteristika der von der Reform Betroffenen (insgesamt 12 Punkte)

Wir wollen bestimmen wer mittelbar von der Reform betroffen ist. In der folgenden Zelle codieren wir mittelbar betroffene Personen in der Spale `betroffen_von_reform` als `True` und bilden daraus einen neuen Datensatz `reform_betroffene`.

In [ ]:
soep_daten_mit_alg2 = soep_daten.reset_index().join(
    gettsim_ergebnisse_status_quo["arbeitsl_geld_2_m_hh"],
)

soep_daten_mit_alg2["betroffen_von_reform"] = np.where(
    (soep_daten_mit_alg2["arbeitsl_geld_2_m_hh"] == 0)
    & (soep_daten_mit_alg2["bruttolohn_m"] <= minijob_grenze)
    & ~soep_daten_mit_alg2["kind"]
    & soep_daten_mit_alg2["hauptverdiener_versichert"],
    True,  # noqa: FBT003
    False,  # noqa: FBT003
)

soep_daten_mit_alg2["betroffen_von_reform"] = soep_daten_mit_alg2.groupby("hh_id")[
    "betroffen_von_reform"
].transform(any)

ergebnisse_status_quo = ergebnisse_status_quo.drop(
    columns=["betroffen_von_reform"],
    errors="ignore",
).join(soep_daten_mit_alg2[["betroffen_von_reform"]])

reform_betroffene = ergebnisse_status_quo.query("betroffen_von_reform == True")

#### Aufgabe 4.2.1: Häufigkeit der von der Reform betroffenen Haushalte (6 Punkte)

Wie viel Prozent aller Haushalte wären ohne Verhaltensanpassung von der Reform betroffen?

#### Aufgabe 4.2.2: Einkommen der betroffenen Haushalte (6 Punkte)

Sind tendenziell reichere oder ärmere Haushalte betroffen? Vergleichen Sie das Nettoäquivalenzeinkommen der betroffenen mit denen der Grundgesamtheit.

### Aufgabe 4.3: Ungleichheit im Reformszenario (insgesamt 7 Punkte)

Wir wiederholen das Berechnen der Steuern und Transfers. Diesmal nutzen wir aber die Funktion `krankenv_beitr_reform_m` anstelle der Funktion `krankenv_beitr_status_quo_m`.

In [ ]:
gettsim_ergebnisse_reform = compute_taxes_and_transfers(
    data=soep_daten.reset_index(),
    params=params_dict,
    functions=[
        policy_func_dict,
        {"krankenv_beitr_m": krankenv_beitr_reform_m},
    ],
    targets=[
        "kindergeld_m_hh",
        "arbeitsl_geld_m",
        "arbeitsl_geld_2_m_hh",
        "wohngeld_m_hh",
        "kinderzuschl_m_hh",
        "eink_st_tu",
        "soli_st_tu",
        "sum_eink_tu",
        "krankenv_beitr_m",
        "ges_pflegev_beitr_m",
        "ges_rentenv_beitr_m",
        "arbeitsl_v_beitr_m",
    ],
)

gettsim_ergebnisse_reform = gettsim_ergebnisse_reform.join(
    soep_daten.reset_index()["hh_id"],
)

gettsim_ergebnisse_reform

Außerdem wiederholen wir die Schritte zu Vorbereitung um das monatliche verfügbare Haushaltseinkommen bestimmen zu können.

In [ ]:
ergebnisse_reform = (
    gettsim_ergebnisse_reform.reset_index()
    .groupby("hh_id")
    .agg(
        {
            "kindergeld_m_hh": lambda x: x.max(),
            "eink_st_tu": lambda x: x.max() / 12,
            "soli_st_tu": lambda x: x.max() / 12,
            "arbeitsl_geld_2_m_hh": lambda x: x.max(),
            "arbeitsl_geld_m": lambda x: x.sum(),
            "wohngeld_m_hh": lambda x: x.max(),
            "kinderzuschl_m_hh": lambda x: x.max(),
            "sum_eink_tu": lambda x: x.max() / 12,
            "krankenv_beitr_m": lambda x: x.sum(),
            "ges_pflegev_beitr_m": lambda x: x.sum(),
            "ges_rentenv_beitr_m": lambda x: x.sum(),
            "arbeitsl_v_beitr_m": lambda x: x.sum(),
        },
    )
)

# Variablen korrekt benennen
ergebnisse_reform = ergebnisse_reform.rename(
    columns={
        "eink_st_tu": "einkommensteuer_m_tu",
        "soli_st_tu": "soli_m_tu",
        "sum_eink_tu": "bruttolohn_m_hh",
        "arbeitsl_geld_m": "arbeitsl_geld_m_hh",
        "krankenv_beitr_m": "krankenv_beitr_m_hh",
        "ges_pflegev_beitr_m": "ges_pflegev_beitr_m_hh",
        "ges_rentenv_beitr_m": "ges_rentenv_beitr_m_hh",
        "arbeitsl_v_beitr_m": "arbeitsl_v_beitr_m_hh",
    },
)

ergebnisse_reform = (
    ergebnisse_reform.join(
        soep_daten[
            [
                "hh_gewicht",
                "kapital_eink_m_hh",
                "anz_erwachsene",
                "anz_kinder_bis_13",
                "anz_kinder_ab_14",
            ]
        ],
    )
    .reset_index()
    .drop_duplicates(["hh_id"])
)

ergebnisse_reform["verfügbares_einkommen_m_hh"] = (
    ergebnisse_reform["bruttolohn_m_hh"]
    + ergebnisse_reform["kapital_eink_m_hh"]
    + ergebnisse_reform["kindergeld_m_hh"]
    + ergebnisse_reform["arbeitsl_geld_m_hh"]
    + ergebnisse_reform["arbeitsl_geld_2_m_hh"]
    + ergebnisse_reform["kinderzuschl_m_hh"]
    + ergebnisse_reform["wohngeld_m_hh"]
    - ergebnisse_reform["einkommensteuer_m_tu"]
    - ergebnisse_reform["soli_m_tu"]
    - ergebnisse_reform["krankenv_beitr_m_hh"]
    - ergebnisse_reform["ges_pflegev_beitr_m_hh"]
    - ergebnisse_reform["ges_rentenv_beitr_m_hh"]
    - ergebnisse_reform["arbeitsl_v_beitr_m_hh"]
)

ergebnisse_reform

#### Aufgabe 4.3.1: Berechnung des Nettoäquivalenzeinkommens (5 Punkte)

Berechnen Sie das verfügbare Nettoäquivalenzeinkommen mithilfe der OECD Gewichtung.

#### Aufgabe 4.3.2: Berechnung des Gini-Koeffizienten (2 Punkte)

Berechnen Sie den Gini Koeffizienten im Reformszenario.

### Aufgabe 4.4: Interpretation der Verteilungseffekte (15 Punkte)

Nehmen Sie an, dass der im Status Quo berechnete Gini-Koeffizient die Realität abbildet. Wie Sie sehen (sollten), hat die Reform keine nennenswerten Auswirkungen auf den Gini-Koeffizienten in unseren Berechnungen.

Erwarten Sie, dass das ebenso wäre, wenn die solche Reform tatsächlich durchgeführt würde? Warum, warum nicht?

## Aufgabe 5: Budgetwirkung der Reform (insgesamt 30 Punkte)

Motiviert wurde der Reformvorschlag u.a. durch den erwarteten Kostendruck auf die gesetzliche Krankenversicherung durch den demografischen Wandel. Daher möchten wir die Budgetwirkung der Reform analysieren. 

### Aufgabe 5.1: Berechnung des Budgets im Status Quo (10 Punkte)

Errechnen Sie die Summe der Krankenversicherungsbeiträge aller Haushalte **im Jahr 2019 im Status Quo**.

**Tipp:** Die Variable `hh_gewicht` im DataFrame `ergebnisse_status_quo` gibt an wie viele deutsche Haushalte durch den Haushalt im Datensatz repräsentiert werden. Multiplizieren Sie Ihr Ergebnis mit dem Faktor 2.4. Diese Skalierung ist notwendig, weil wir nur 4_000 Haushalte betrachten, nicht das gesamte SOEP.

### Aufgabe 5.2: Unterschätzen der tatsächlichen Einnahmen (8 Punkte)

Das tatsächliche Volumen des Gesundheitsfonds betrug im Jahr 2019 insgesamt 250 Mrd €. Nennen Sie zwei Gründe warum wir die Einnahmen in der obigen Aufgabe unterschätzen. Zwei Stichworte genügen.

### Aufgabe 5.3: Berechnung des Budgets im Reformszenario (10 Punkte)

Errechnen Sie die Summe der Krankenversicherungsbeiträge aller Haushalte im **Jahr 2019 im Reformszenario**. Skalieren Sie Ihr Ergebnis erneut mit 2.4.

### Aufgabe 5.4: Entlastende Wirkung der Reform (2 Punkte)

Um wie viel Prozent kann der Bundeszuschuss durch die Reform sinken, wenn das Volumen des Gesundheitsfonds konstant gehalten werden soll?

## Aufgabe 6: Belastung der Haushalte durch das Sozialversicherungssystem (12 Punkte)

Beziehen Sie Stellung zu den folgenden beiden Aussagen. Korrigieren Sie sie, falls notwendig.

Die Abschaffung der kostenlosen Familienversicherung für Ehepartner bewirkt für Löhne im Minijob-Bereich einen Anstieg der **Grenzbelastung**.

Die **Grenzsteuersätze** sinken wenn das Einkommen die Beitragsbemessungsgrenze übersteigt.

## Aufgabe 7: Klausurfrage aus dem Kurs (6 Punkte)

Beantworten Sie folgende Frage.

Für manche Bürgergeldempfänger:innen lohnt es sich nicht das Arbeitsangebot auszuweiten. Welche Möglichkeiten hat der Staat diesen Umstand zu ändern?